In [1]:
import sys
import os
import numpy as np
import torch
import torch.utils.data as du
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
import time
import optuna

from tqdm import tqdm
from optuna.trial import TrialState

os.chdir('../DrugCell/code')

from drugcell_NN import *

In [2]:
def create_term_mask(term_direct_gene_map, gene_dim):

    term_mask_map = {}

    for term, gene_set in term_direct_gene_map.items():

        mask = torch.zeros(len(gene_set), gene_dim)

        for i, gene_id in enumerate(gene_set):
            mask[i, gene_id] = 1

        mask_gpu = torch.autograd.Variable(mask.cuda(CUDA_ID))

        term_mask_map[term] = mask_gpu

    return term_mask_map

In [3]:
def get_data():

    torch.set_printoptions(precision=5)
    train_data, cell2id_mapping, drug2id_mapping = prepare_train_data(
        "../data_rcellminer/train_DNA.txt", 
        "../data_rcellminer/val_DNA.txt",
        "../data_rcellminer/cell2ind.txt", 
        "../data_rcellminer/drug2ind.txt",
    )

    gene2id_mapping = load_mapping("../data_rcellminer/gene2ind.txt")
    cell_features = np.genfromtxt("../data_rcellminer/cell2mut.txt", delimiter=",")
    drug_features = np.genfromtxt("../data_rcellminer/drug2fingerprint.csv", delimiter=",")

    num_cells = len(cell2id_mapping)
    num_drugs = len(drug2id_mapping)
    num_genes = len(gene2id_mapping)
    drug_dim = len(drug_features[0, :])

    dG, root, term_size_map, term_direct_gene_map = load_ontology("../data_rcellminer/go.txt", gene2id_mapping)

    num_hiddens_genotype = 6
    num_hiddens_drug = [512, 256, 64, 8]
    num_hiddens_final = 6

    return (root, term_size_map, term_direct_gene_map, dG, train_data, num_genes, drug_dim, cell_features, drug_features,)

In [4]:
def objective(trial):
    (root, term_size_map, term_direct_gene_map, dG, train_data, gene_dim, drug_dim, cell_features, drug_features) = get_data()

    train_epochs = 300
    num_hiddens_genotype = trial.suggest_int("num_hiddens_genotype", 1, 6)
    num_hiddens_final = trial.suggest_int("num_hiddens_final", 1, 6)
    i = trial.suggest_int("i", 1, 4)
    
    if i == 1:
        num_hiddens_drug = [256, 64, 4]
    elif i == 2:
        num_hiddens_drug = [256, 64, 8]
    elif i == 3:
        num_hiddens_drug = [512, 256, 64, 8]
    else:
        num_hiddens_drug = [512, 256, 64, 8, 4]
    
    model = drugcell_nn(term_size_map, term_direct_gene_map, dG, gene_dim, drug_dim, root, num_hiddens_genotype, num_hiddens_drug, num_hiddens_final)

    train_feature, train_label, test_feature, test_label = train_data
    train_label_gpu = torch.autograd.Variable(train_label.cuda(CUDA_ID))
    test_label_gpu = torch.autograd.Variable(test_label.cuda(CUDA_ID))

    model.cuda(CUDA_ID)

    lr = trial.suggest_float("lr", 1e-5, 1e-1, log=True)

    optimizer = torch.optim.Adam(model.parameters(), lr=lr, betas=(0.9, 0.99), eps=1e-05)
    term_mask_map = create_term_mask(model.term_direct_gene_map, gene_dim)
    optimizer.zero_grad()

    for name, param in model.named_parameters():
        term_name = name.split("_")[0]

        if "_direct_gene_layer.weight" in name:
            param.data = torch.mul(param.data, term_mask_map[term_name]) * 0.1
        else:
            param.data = param.data * 0.1

    batch_size = trial.suggest_categorical("batch_size", [1000, 2000, 3000])
    train_loader = du.DataLoader(du.TensorDataset(train_feature, train_label), batch_size=batch_size, shuffle=False,)

    for epoch in tqdm(range(train_epochs)):
        model.train()
        train_predict = torch.zeros(0, 0).cuda(CUDA_ID)

        for i, (inputdata, labels) in enumerate(train_loader):
            features = build_input_vector(inputdata, cell_features, drug_features)
            cuda_features = torch.autograd.Variable(features.cuda(CUDA_ID))
            cuda_labels = torch.autograd.Variable(labels.cuda(CUDA_ID))
            optimizer.zero_grad()
            aux_out_map, _ = model(cuda_features)

            if train_predict.size()[0] == 0:
                train_predict = aux_out_map["final"].data
            else:
                train_predict = torch.cat([train_predict, aux_out_map["final"].data], dim=0)

            total_loss = 0
            for name, output in aux_out_map.items():
                loss = nn.MSELoss()
                if name == "final":
                    total_loss += loss(output, cuda_labels)
                else:  # change 0.2 to smaller one for big terms
                    total_loss += 0.2 * loss(output, cuda_labels)

            total_loss.backward()

            for name, param in model.named_parameters():
                if "_direct_gene_layer.weight" not in name:
                    continue
                term_name = name.split("_")[0]
                param.grad.data = torch.mul(param.grad.data, term_mask_map[term_name])

            optimizer.step()

        trial.report(total_loss, epoch)

        if trial.should_prune():
            raise optuna.exceptions.TrialPruned()

    return total_loss

In [ ]:
CUDA_ID = 0
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=300)
study.trials_dataframe().to_csv("study_history.csv")

[I 2022-08-19 18:12:16,632] A new study created in memory with name: no-name-74c10be2-ae3a-410e-a522-fde9c8f5423e


Total number of cell lines = 55
Total number of drugs = 214
There are 2729 genes
There are 1 roots: GO:0008150
There are 2086 terms
There are 1 connected componenets
term	GO:0007005	term_size	63	num_hiddens	1
term	GO:0007006	term_size	25	num_hiddens	1
term	GO:0008637	term_size	19	num_hiddens	1
term	GO:0006281	term_size	88	num_hiddens	1
term	GO:0006284	term_size	17	num_hiddens	1
term	GO:0006283	term_size	13	num_hiddens	1
term	GO:0019985	term_size	10	num_hiddens	1
term	GO:0000724	term_size	13	num_hiddens	1
term	GO:0006303	term_size	15	num_hiddens	1
term	GO:0051052	term_size	104	num_hiddens	1
term	GO:0044030	term_size	12	num_hiddens	1
term	GO:0051054	term_size	70	num_hiddens	1
term	GO:0010569	term_size	8	num_hiddens	1
term	GO:0045830	term_size	9	num_hiddens	1
term	GO:0045739	term_size	17	num_hiddens	1
term	GO:2000279	term_size	13	num_hiddens	1
term	GO:0032212	term_size	15	num_hiddens	1
term	GO:0051973	term_size	14	num_hiddens	1
term	GO:1903047	term_size	142	num_hiddens	1
term	GO:0000070	t

100%|██████████| 300/300 [1:25:29<00:00, 17.10s/it]
[I 2022-08-19 19:37:49,563] Trial 0 finished with value: 375.5171813964844 and parameters: {'num_hiddens_genotype': 1, 'num_hiddens_final': 5, 'i': 2, 'lr': 1.2054672209311313e-05, 'batch_size': 1000}. Best is trial 0 with value: 375.5171813964844.


Total number of cell lines = 55
Total number of drugs = 214
There are 2729 genes
There are 1 roots: GO:0008150
There are 2086 terms
There are 1 connected componenets
term	GO:0007005	term_size	63	num_hiddens	3
term	GO:0007006	term_size	25	num_hiddens	3
term	GO:0008637	term_size	19	num_hiddens	3
term	GO:0006281	term_size	88	num_hiddens	3
term	GO:0006284	term_size	17	num_hiddens	3
term	GO:0006283	term_size	13	num_hiddens	3
term	GO:0019985	term_size	10	num_hiddens	3
term	GO:0000724	term_size	13	num_hiddens	3
term	GO:0006303	term_size	15	num_hiddens	3
term	GO:0051052	term_size	104	num_hiddens	3
term	GO:0044030	term_size	12	num_hiddens	3
term	GO:0051054	term_size	70	num_hiddens	3
term	GO:0010569	term_size	8	num_hiddens	3
term	GO:0045830	term_size	9	num_hiddens	3
term	GO:0045739	term_size	17	num_hiddens	3
term	GO:2000279	term_size	13	num_hiddens	3
term	GO:0032212	term_size	15	num_hiddens	3
term	GO:0051973	term_size	14	num_hiddens	3
term	GO:1903047	term_size	142	num_hiddens	3
term	GO:0000070	t

100%|██████████| 300/300 [1:27:32<00:00, 17.51s/it]
[I 2022-08-19 21:05:24,643] Trial 1 finished with value: 264.595703125 and parameters: {'num_hiddens_genotype': 3, 'num_hiddens_final': 5, 'i': 3, 'lr': 0.0014581309485455, 'batch_size': 1000}. Best is trial 1 with value: 264.595703125.


...

  2%|▏         | 7/300 [01:09<48:42,  9.97s/it]
[I 2022-08-20 19:59:21,253] Trial 70 pruned. 


Total number of cell lines = 55
Total number of drugs = 214
There are 2729 genes
There are 1 roots: GO:0008150
There are 2086 terms
There are 1 connected componenets
term	GO:0007005	term_size	63	num_hiddens	6
term	GO:0007006	term_size	25	num_hiddens	6
term	GO:0008637	term_size	19	num_hiddens	6
term	GO:0006281	term_size	88	num_hiddens	6
term	GO:0006284	term_size	17	num_hiddens	6
term	GO:0006283	term_size	13	num_hiddens	6
term	GO:0019985	term_size	10	num_hiddens	6
term	GO:0000724	term_size	13	num_hiddens	6
term	GO:0006303	term_size	15	num_hiddens	6
term	GO:0051052	term_size	104	num_hiddens	6
term	GO:0044030	term_size	12	num_hiddens	6
term	GO:0051054	term_size	70	num_hiddens	6
term	GO:0010569	term_size	8	num_hiddens	6
term	GO:0045830	term_size	9	num_hiddens	6
term	GO:0045739	term_size	17	num_hiddens	6
term	GO:2000279	term_size	13	num_hiddens	6
term	GO:0032212	term_size	15	num_hiddens	6
term	GO:0051973	term_size	14	num_hiddens	6
term	GO:1903047	term_size	142	num_hiddens	6
term	GO:0000070	t

100%|██████████| 300/300 [43:30<00:00,  8.70s/it]
[I 2022-08-20 20:42:54,143] Trial 71 finished with value: 235.33786010742188 and parameters: {'num_hiddens_genotype': 6, 'num_hiddens_final': 1, 'i': 1, 'lr': 0.05653915496375114, 'batch_size': 2000}. Best is trial 59 with value: 235.23899841308594.


Total number of cell lines = 55
Total number of drugs = 214
There are 2729 genes
There are 1 roots: GO:0008150
There are 2086 terms
There are 1 connected componenets
term	GO:0007005	term_size	63	num_hiddens	6
term	GO:0007006	term_size	25	num_hiddens	6
term	GO:0008637	term_size	19	num_hiddens	6
term	GO:0006281	term_size	88	num_hiddens	6
term	GO:0006284	term_size	17	num_hiddens	6
term	GO:0006283	term_size	13	num_hiddens	6
term	GO:0019985	term_size	10	num_hiddens	6
term	GO:0000724	term_size	13	num_hiddens	6
term	GO:0006303	term_size	15	num_hiddens	6
term	GO:0051052	term_size	104	num_hiddens	6
term	GO:0044030	term_size	12	num_hiddens	6
term	GO:0051054	term_size	70	num_hiddens	6
term	GO:0010569	term_size	8	num_hiddens	6
term	GO:0045830	term_size	9	num_hiddens	6
term	GO:0045739	term_size	17	num_hiddens	6
term	GO:2000279	term_size	13	num_hiddens	6
term	GO:0032212	term_size	15	num_hiddens	6
term	GO:0051973	term_size	14	num_hiddens	6
term	GO:1903047	term_size	142	num_hiddens	6
term	GO:0000070	t

100%|█████████▉| 299/300 [43:05<00:08,  8.68s/it]